In [1]:
#variables:
#name of the node, a count
#nodelink used to link similar items
#parent vaiable used to refer to the parent of the node in the tree
#node contains an empty dictionary for the children in the node
class treeNode:
    def __init__(self, nameValue, numOccur, parentNode):
        self.name = nameValue
        self.count = numOccur
        self.nodeLink = None
        self.parent = parentNode      #needs to be updated
        self.children = {} 
#increments the count variable with a given amount    
    def inc(self, numOccur):
        self.count += numOccur
#display tree in text. Useful for debugging        
    def disp(self, ind=1):
        print ('  '*ind, self.name, ' ', self.count)
        for child in self.children.values():
            child.disp(ind+1)


In [2]:
def createTree(dataSet, minSup=1): #create FP-tree from dataset but don't mine
    headerTable = {}
    #go over dataSet twice
    for trans in dataSet:#first pass counts frequency of occurance
        for item in trans:
            headerTable[item] = headerTable.get(item, 0) + dataSet[trans]
    for k in list(headerTable):  #remove items not meeting minSup
        if headerTable[k] < minSup: 
            del(headerTable[k])
    freqItemSet = set(headerTable.keys())
    #print 'freqItemSet: ',freqItemSet
    if len(freqItemSet) == 0: return None, None  #if no items meet min support -->get out
    for k in headerTable:
        headerTable[k] = [headerTable[k], None] #reformat headerTable to use Node link 
    #print 'headerTable: ',headerTable
    retTree = treeNode('Null Set', 1, None) #create tree
    for tranSet, count in dataSet.items():  #go through dataset 2nd time
        localD = {}
        for item in tranSet:  #put transaction items in order
            if item in freqItemSet:
                localD[item] = headerTable[item][0]
        if len(localD) > 0:
            orderedItems = [v[0] for v in sorted(localD.items(), key=lambda p: p[1], reverse=True)]
            updateTree(orderedItems, retTree, headerTable, count)#populate tree with ordered freq itemset
    return retTree, headerTable #return tree and header table


In [3]:
def updateTree(items, inTree, headerTable, count):
    if items[0] in inTree.children:#check if orderedItems[0] in retTree.children
        inTree.children[items[0]].inc(count) #incrament count
    else:   #add items[0] to inTree.children
        inTree.children[items[0]] = treeNode(items[0], count, inTree)
        if headerTable[items[0]][1] == None: #update header table 
            headerTable[items[0]][1] = inTree.children[items[0]]
        else:
            updateHeader(headerTable[items[0]][1], inTree.children[items[0]])
    if len(items) > 1:#call updateTree() with remaining ordered items
        updateTree(items[1::], inTree.children[items[0]], headerTable, count)


In [4]:
def updateHeader(nodeToTest, targetNode):   #this version does not use recursion
    while (nodeToTest.nodeLink != None):    #Do not use recursion to traverse a linked list!
        nodeToTest = nodeToTest.nodeLink
    nodeToTest.nodeLink = targetNode

In [9]:
def loadSimpDat():
    simpDat = [['M','O','N','K','E','Y'],
               ['D','O','N','K','E','Y'],
               ['M','U','C','K','Y'],
               ['C','O','O','K','I','E'],
               ['M','A','K','E']
              ]
    return simpDat

In [10]:
def createInitSet(dataSet):
    retDict = {}
    for trans in dataSet:
        retDict[frozenset(trans)] = 1
    return retDict

In [11]:
simpDat = loadSimpDat()
simpDat

[['M', 'O', 'N', 'K', 'E', 'Y'],
 ['D', 'O', 'N', 'K', 'E', 'Y'],
 ['M', 'U', 'C', 'K', 'Y'],
 ['C', 'O', 'O', 'K', 'I', 'E'],
 ['M', 'A', 'K', 'E']]

In [12]:
initSet = createInitSet(simpDat)
initSet

{frozenset({'E', 'K', 'M', 'N', 'O', 'Y'}): 1,
 frozenset({'D', 'E', 'K', 'N', 'O', 'Y'}): 1,
 frozenset({'C', 'K', 'M', 'U', 'Y'}): 1,
 frozenset({'C', 'E', 'I', 'K', 'O'}): 1,
 frozenset({'A', 'E', 'K', 'M'}): 1}

In [13]:
#The FP-tree
myFPtree, myHeaderTab = createTree(initSet, 3)
myFPtree.disp()

   Null Set   1
     K   5
       E   4
         O   3
           M   1
             Y   1
           Y   1
         M   1
       M   1
         Y   1


In [14]:
def ascendTree(leafNode, prefixPath): #ascends from leaf node to root
    if leafNode.parent != None:
        prefixPath.append(leafNode.name)
        ascendTree(leafNode.parent, prefixPath)

In [17]:
"""def findPrefixPath(basePat, treeNode): #treeNode comes from header table
    condPats = {}
    while treeNode != None:
        prefixPath = []
        ascendTree(treeNode, prefixPath)
        if len(prefixPath) > 1: 
            condPats[frozenset(prefixPath[1:])] = treeNode.count
        treeNode = treeNode.nodeLink
    return condPats"""

'def findPrefixPath(basePat, treeNode): #treeNode comes from header table\n    condPats = {}\n    while treeNode != None:\n        prefixPath = []\n        ascendTree(treeNode, prefixPath)\n        if len(prefixPath) > 1: \n            condPats[frozenset(prefixPath[1:])] = treeNode.count\n        treeNode = treeNode.nodeLink\n    return condPats'

In [19]:
import numpy as np
import pandas as pd
df=pd.read_csv("testr.csv")

lis=np.array(df)

array([[50, ' Self-emp-not-inc', 83311, ..., 13, ' United-States',
        ' <=50K'],
       [38, ' Private', 215646, ..., 40, ' United-States', ' <=50K'],
       [53, ' Private', 234721, ..., 40, ' United-States', ' <=50K'],
       ...,
       [58, ' Private', 151910, ..., 40, ' United-States', ' <=50K'],
       [22, ' Private', 201490, ..., 20, ' United-States', ' <=50K'],
       [52, ' Self-emp-inc', 287927, ..., 40, ' United-States', ' >50K']],
      dtype=object)

In [22]:
initSet = createInitSet(lis)
initSet

{frozenset({' <=50K',
            ' Bachelors',
            ' Exec-managerial',
            ' Husband',
            ' Male',
            ' Married-civ-spouse',
            ' Self-emp-not-inc',
            ' United-States',
            ' White',
            0,
            13,
            50,
            83311}): 1,
 frozenset({' <=50K',
            ' Divorced',
            ' HS-grad',
            ' Handlers-cleaners',
            ' Male',
            ' Not-in-family',
            ' Private',
            ' United-States',
            ' White',
            0,
            215646,
            38,
            40,
            9}): 1,
 frozenset({' 11th',
            ' <=50K',
            ' Black',
            ' Handlers-cleaners',
            ' Husband',
            ' Male',
            ' Married-civ-spouse',
            ' Private',
            ' United-States',
            0,
            234721,
            40,
            53,
            7}): 1,
 frozenset({' <=50K',
            ' Bachelors

In [24]:
#The FP-tree
myFPtree, myHeaderTab = createTree(initSet, 5)
myFPtree.disp()

   Null Set   1
     0   32536
        United-States   29152
          White   25605
            <=50K   18903
              Male   3630
                Married-civ-spouse   1249
                  Husband   1238
                   13   179
                      Bachelors   178
                        Exec-managerial   36
                         50   6
                            Self-emp-not-inc   5
                             47   1
                             35   1
                             58   1
                             27   1
                            Self-emp-inc   1
                             49   1
                          Self-emp-not-inc   9
                           30   1
                             47   1
                               102359   1
                           60   3
                             56   1
                             44   1
                             38   1
                           51   1
                             70   1


                       4   1
                          7th-8th   1
                           58   1
                       8   1
                          12th   1
                           64   1
                     14   4
                        Masters   4
                         64   1
                           2   1
                         55   1
                           18   1
                         8   1
                           70   1
                         2   1
                           67   1
                     15   2
                       5   1
                          9th   1
                           67   1
                       16   1
                          Prof-school   1
                           64   1
                     20   11
                       3   2
                          5th-6th   2
                           77   1
                           84   1
                       5   1
                          9th   1
                  

                           43   1
                             17   1
                         30   1
                            Transport-moving   1
                             37   1
                         32   1
                            Protective-serv   1
                             99   1
                               113838   1
                         36   1
                           48   1
                              Protective-serv   1
                       60   4
                          Federal-gov   1
                           29   1
                              Protective-serv   1
                          Self-emp-inc   2
                            Farming-fishing   2
                             49   1
                             53   1
                          State-gov   1
                            Protective-serv   1
                             53   1
                       45   2
                          Local-gov   2
                          

                             67   1
                               1797   1
                             75   1
                             82   1
                         48   1
                            Farming-fishing   1
                             98   1
                               185385   1
                         42   1
                            Farming-fishing   1
                             15   1
                         37   1
                            Farming-fishing   1
                             72   1
                          Machine-op-inspct   1
                           25   1
                             41   1
                         38   1
                            Farming-fishing   1
                             41   1
                         55   2
                            Farming-fishing   2
                             67   1
                             51   1
                       45   8
                          Local-gov   2
      

                          Craft-repair   1
                            Self-emp-inc   1
                             64   1
                               2635   1
                        Prof-specialty   8
                          Local-gov   1
                           30   1
                             44   1
                          Self-emp-not-inc   5
                           30   2
                             25   1
                             37   1
                               3137   1
                           35   1
                             28   1
                           60   1
                             46   1
                           34   1
                             51   1
                          Federal-gov   1
                           8   1
                             64   1
                         50   1
                            State-gov   1
                             52   1
                        State-gov   5
                     

...

                           65   1
                              Yugoslavia   1
                    ?   1
                     14   1
                        Masters   1
                          Transport-moving   1
                           38   1
                             72   1
                               22245   1
                    Prof-specialty   11
                     50   2
                        ?   1
                         14   1
                            Masters   1
                             55   1
                               15024   1
                                 98361   1
                       11   1
                          Assoc-voc   1
                           55   1
                             1977   1
                                Germany   1
                     45   1
                       14   1
                          Masters   1
                           36   1
                              England   1
                     60  

                              7th-8th   1
                     10   14
                        Some-college   14
                          Craft-repair   4
                           54   1
                              Germany   1
                               3103   1
                                 139703   1
                           36   1
                              Canada   1
                            ?   1
                             36   1
                               361888   1
                           45   1
                              ?   1
                               1902   1
                         45   1
                            Handlers-cleaners   1
                              Germany   1
                          Prof-specialty   4
                           55   1
                              Poland   1
                           47   1
                              Scotland   1
                           52   1
                              Ge

                       15   1
                         41   1
                            Prof-school   1
                              Japan   1
               9   3
                  HS-grad   3
                    >50K   3
                      Exec-managerial   2
                        Wife   2
                         36   1
                           43   1
                              Portugal   1
                         42   1
                           33   1
                              Canada   1
                               101345   1
                      Adm-clerical   1
                       50   1
                          Wife   1
                           43   1
                              Canada   1
           40   13
              Married-civ-spouse   11
                Female   11
                  >50K   7
                    Adm-clerical   1
                      Wife   1
                       12   1
                          Assoc-acdm   1
           

                           73   1
                              Poland   1
                    Some-college   7
                      Sales   3
                       50   1
                          Self-emp-not-inc   1
                           43   1
                              Mexico   1
                               7298   1
                        Self-emp-not-inc   1
                         60   1
                           41   1
                              Mexico   1
                       60   1
                         38   1
                            Self-emp-inc   1
                              Cuba   1
                               1485   1
                      Exec-managerial   3
                       50   1
                          Self-emp-inc   1
                            Germany   1
                       60   1
                          Self-emp-inc   1
                           36   1
                              Yugoslavia   1
                   

                        Local-gov   1
                          Tech-support   1
                            England   1
                             8614   1
            Married-civ-spouse   9
              Female   9
               9   3
                  HS-grad   3
                    >50K   3
                      Prof-specialty   1
                        Self-emp-not-inc   1
                          Wife   1
                           44   1
                              Italy   1
                      Adm-clerical   1
                        ?   1
                          Wife   1
                            Self-emp-inc   1
                             64   1
                               20051   1
                      ?   1
                        Wife   1
                         62   1
                           5178   1
                              Scotland   1
                >50K   6
                  Exec-managerial   1
                   30   1
                   

In [27]:
from csv import reader
from collections import defaultdict
from itertools import chain, combinations

class Node:
    def __init__(self, itemName, frequency, parentNode):
        self.itemName = itemName
        self.count = frequency
        self.parent = parentNode
        self.children = {}
        self.next = None

    def increment(self, frequency):
        self.count += frequency

    def display(self, ind=1):
        print('  ' * ind, self.itemName, ' ', self.count)
        for child in list(self.children.values()):
            child.display(ind+1)

def getFromFile(fname):
    itemSetList = []
    frequency = []
    
    with open(fname, 'r') as file:
        csv_reader = reader(file)
        for line in csv_reader:
            line = list(filter(None, line))
            itemSetList.append(line)
            frequency.append(1)

    return itemSetList, frequency

def constructTree(itemSetList, frequency, minSup):
    headerTable = defaultdict(int)
    # Counting frequency and create header table
    for idx, itemSet in enumerate(itemSetList):
        for item in itemSet:
            headerTable[item] += frequency[idx]

    # Deleting items below minSup
    headerTable = dict((item, sup) for item, sup in headerTable.items() if sup >= minSup)
    if(len(headerTable) == 0):
        return None, None

    # HeaderTable column [Item: [frequency, headNode]]
    for item in headerTable:
        headerTable[item] = [headerTable[item], None]

    # Init Null head node
    fpTree = Node('Null', 1, None)
    # Update FP tree for each cleaned and sorted itemSet
    for idx, itemSet in enumerate(itemSetList):
        itemSet = [item for item in itemSet if item in headerTable]
        itemSet.sort(key=lambda item: headerTable[item][0], reverse=True)
        # Traverse from root to leaf, update tree with given item
        currentNode = fpTree
        for item in itemSet:
            currentNode = updateTree(item, currentNode, headerTable, frequency[idx])

    return fpTree, headerTable

def updateHeaderTable(item, targetNode, headerTable):
    if(headerTable[item][1] == None):
        headerTable[item][1] = targetNode
    else:
        currentNode = headerTable[item][1]
        # Traverse to the last node then link it to the target
        while currentNode.next != None:
            currentNode = currentNode.next
        currentNode.next = targetNode

def updateTree(item, treeNode, headerTable, frequency):
    if item in treeNode.children:
        # If the item already exists, increment the count
        treeNode.children[item].increment(frequency)
    else:
        # Create a new branch
        newItemNode = Node(item, frequency, treeNode)
        treeNode.children[item] = newItemNode
        # Link the new branch to header table
        updateHeaderTable(item, newItemNode, headerTable)

    return treeNode.children[item]

def ascendFPtree(node, prefixPath):
    if node.parent != None:
        prefixPath.append(node.itemName)
        ascendFPtree(node.parent, prefixPath)

def findPrefixPath(basePat, headerTable):
    # First node in linked list
    treeNode = headerTable[basePat][1] 
    condPats = []
    frequency = []
    while treeNode != None:
        prefixPath = []
        # From leaf node all the way to root
        ascendFPtree(treeNode, prefixPath)  
        if len(prefixPath) > 1:
            # Storing the prefix path and it's corresponding count
            condPats.append(prefixPath[1:])
            frequency.append(treeNode.count)

        # Go to next node
        treeNode = treeNode.next  
    return condPats, frequency

def mineTree(headerTable, minSup, preFix, freqItemList):
    # Sort the items with frequency and create a list
    sortedItemList = [item[0] for item in sorted(list(headerTable.items()), key=lambda p:p[1][0])] 
    # Start with the lowest frequency
    for item in sortedItemList:  
        # Pattern growth is achieved by the concatenation of suffix pattern with frequent patterns generated from conditional FP-tree
        newFreqSet = preFix.copy()
        newFreqSet.add(item)
        freqItemList.append(newFreqSet)
        # Find all prefix path, constrcut conditional pattern base
        conditionalPattBase, frequency = findPrefixPath(item, headerTable) 
        # Construct conditonal FP Tree with conditional pattern base
        conditionalTree, newHeaderTable = constructTree(conditionalPattBase, frequency, minSup) 
        if newHeaderTable != None:
            # Mining recursively on the tree
            mineTree(newHeaderTable, minSup,
                       newFreqSet, freqItemList)

def powerset(s):
    return chain.from_iterable(combinations(s, r) for r in range(1, len(s)))

def getSupport(testSet, itemSetList):
    count = 0
    for itemSet in itemSetList:
        if(set(testSet).issubset(itemSet)):
            count += 1
    return count

def associationRule(freqItemSet, itemSetList, minConf):
    rules = []
    for itemSet in freqItemSet:
        subsets = powerset(itemSet)
        itemSetSup = getSupport(itemSet, itemSetList)
        for s in subsets:
            confidence = float(itemSetSup / getSupport(s, itemSetList))
            if(confidence > minConf):
                rules.append([set(s), set(itemSet.difference(s)), confidence])
    return rules

def getFrequencyFromList(itemSetList):
    frequency = [1 for i in range(len(itemSetList))]
    return frequency

In [30]:
from collections import defaultdict, OrderedDict
from csv import reader
from itertools import chain, combinations
from optparse import OptionParser


def fpgrowth(itemSetList, minSupRatio, minConf):
    frequency = getFrequencyFromList(itemSetList)
    minSup = len(itemSetList) * minSupRatio
    fpTree, headerTable = constructTree(itemSetList, frequency, minSup)
    if(fpTree == None):
        print('No frequent item set')
    else:
        freqItems = []
        mineTree(headerTable, minSup, set(), freqItems)
        rules = associationRule(freqItems, itemSetList, minConf)
        return freqItems, rules

"""def fpgrowthFromFile(fname, minSupRatio, minConf):
    itemSetList, frequency = getFromFile(fname)
    minSup = len(itemSetList) * minSupRatio
    fpTree, headerTable = constructTree(itemSetList, frequency, minSup)
    if(fpTree == None):
        print('No frequent item set')
    else:
        freqItems = []
        mineTree(headerTable, minSup, set(), freqItems)
        rules = associationRule(freqItems, itemSetList, minConf)
        return freqItems, rules"""



"def fpgrowthFromFile(fname, minSupRatio, minConf):\n    itemSetList, frequency = getFromFile(fname)\n    minSup = len(itemSetList) * minSupRatio\n    fpTree, headerTable = constructTree(itemSetList, frequency, minSup)\n    if(fpTree == None):\n        print('No frequent item set')\n    else:\n        freqItems = []\n        mineTree(headerTable, minSup, set(), freqItems)\n        rules = associationRule(freqItems, itemSetList, minConf)\n        return freqItems, rules"

In [39]:
freqItemSet = fpgrowth(lis, 0.6,0.8)

print(len(freqItemSet))
#print(rules)

2


In [40]:
freqItemSet

([{' Male'},
  {' Male', 0},
  {' Private'},
  {' Private', ' United-States'},
  {' Private', ' United-States', 0},
  {' Private', 0},
  {' Private', 0},
  {' <=50K'},
  {' <=50K', ' White'},
  {' <=50K', ' White', 0},
  {' <=50K', ' United-States'},
  {' <=50K', ' United-States', 0},
  {' <=50K', ' United-States', 0},
  {' <=50K', 0},
  {' <=50K', 0},
  {' White'},
  {' United-States', ' White'},
  {' United-States', ' White', 0},
  {' United-States', ' White', 0},
  {' White', 0},
  {' White', 0},
  {' United-States'},
  {' United-States', 0},
  {' United-States', 0},
  {0},
  {0}],
 [[{' Male'}, {0}, 1.0],
  [{' Private'}, {' United-States'}, 0.8871607331688404],
  [{' Private'}, {' United-States', 0}, 0.8871607331688404],
  [{' Private', 0}, {' United-States'}, 0.8871607331688404],
  [{' Private', ' United-States'}, {0}, 1.0],
  [{' Private'}, {0}, 1.0],
  [{' Private'}, {0}, 1.0],
  [{' <=50K'}, {' White'}, 0.8373316072656661],
  [{' <=50K'}, {' White', 0}, 0.8373316072656661],
  

In [52]:
import itertools
import collections
import collections.abc
import numbers
import typing
from abc import ABC, abstractmethod

from collections import defaultdict
from dataclasses import field, dataclass


In [55]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
High-level implementations of the apriori algorithm.
"""

import typing
#from efficient_apriori.itemsets import itemsets_from_transactions, ItemsetCount
#from efficient_apriori.rules import generate_rules_apriori


def apriori(
    transactions: typing.Union[typing.List[tuple], typing.Callable],
    min_support: float = 0.5,
    min_confidence: float = 0.5,
    max_length: int = 8,
    verbosity: int = 0,
    output_transaction_ids: bool = False,
):
    """
    The classic apriori algorithm as described in 1994 by Agrawal et al.
    The Apriori algorithm works in two phases. Phase 1 iterates over the
    transactions several times to build up itemsets of the desired support
    level. Phase 2 builds association rules of the desired confidence given the
    itemsets found in Phase 1. Both of these phases may be correctly
    implemented by exhausting the search space, i.e. generating every possible
    itemset and checking it's support. The Apriori prunes the search space
    efficiently by deciding apriori if an itemset possibly has the desired
    support, before iterating over the entire dataset and checking.
    Parameters
    ----------
    transactions : list of tuples, list of itemsets.TransactionWithId,
        or a callable returning a generator. Use TransactionWithId's when
        the transactions have ids which should appear in the outputs.
        The transactions may be either a list of tuples, where the tuples must
        contain hashable items. Alternatively, a callable returning a generator
        may be passed. A generator is not sufficient, since the algorithm will
        exhaust it, and it needs to iterate over it several times. Therefore,
        a callable returning a generator must be passed.
    min_support : float
        The minimum support of the rules returned. The support is frequency of
        which the items in the rule appear together in the data set.
    min_confidence : float
        The minimum confidence of the rules returned. Given a rule X -> Y, the
        confidence is the probability of Y, given X, i.e. P(Y|X) = conf(X -> Y)
    max_length : int
        The maximum length of the itemsets and the rules.
    verbosity : int
        The level of detail printing when the algorithm runs. Either 0, 1 or 2.
    output_transaction_ids : bool
        If set to true, the output contains the ids of transactions that
        contain a frequent itemset. The ids are the enumeration of the
        transactions in the sequence they appear.
    Examples
    --------
    >>> transactions = [('a', 'b', 'c'), ('a', 'b', 'd'), ('f', 'b', 'g')]
    >>> itemsets, rules = apriori(transactions, min_confidence=1)
    >>> rules
    [{a} -> {b}]
    """

    itemsets, num_trans = itemsets_from_transactions(
        transactions,
        min_support,
        max_length,
        verbosity,
        output_transaction_ids,
    )

    if itemsets and isinstance(next(iter(itemsets[1].values())), ItemsetCount):
        itemsets_for_rules = _convert_to_counts(itemsets)
    else:
        itemsets_for_rules = itemsets

    rules = generate_rules_apriori(itemsets_for_rules, min_confidence, num_trans, verbosity)
    return itemsets, list(rules)


def _convert_to_counts(itemsets):
    itemsets_counts = {}
    for size, sets in itemsets.items():
        itemsets_counts[size] = {i: c.itemset_count for i, c in sets.items()}
    return itemsets_counts

In [58]:
"""
Implementations of algorithms related to itemsets.
"""

import itertools
import collections
import collections.abc
import numbers
import typing
from abc import ABC, abstractmethod

from collections import defaultdict
from dataclasses import field, dataclass


@dataclass
class ItemsetCount:
    itemset_count: int = 0
    members: set = field(default_factory=set)

    def increment_count(self, transaction_id: int):
        self.itemset_count += 1
        self.members.add(transaction_id)


class _ItemsetCounter(ABC):
    @abstractmethod
    def itemset_counter(self):
        pass

    @abstractmethod
    def get_count(self, count):
        pass

    @abstractmethod
    def singleton_itemsets(self, get_transactions):
        pass

    @abstractmethod
    def large_itemsets(self, counts, min_support, num_transactions):
        pass

    @abstractmethod
    def candidate_itemset_counts(self, C_k, C_k_sets, counter, counts, row, transaction):
        pass


class _Counter(_ItemsetCounter):
    def itemset_counter(self):
        return 0

    def get_count(self, count):
        return count

    def singleton_itemsets(self, get_transactions):
        counts = defaultdict(self.itemset_counter)
        num_transactions = 0
        for _, transaction in get_transactions():
            num_transactions += 1
            for item in transaction:
                counts[item] += 1
        return counts, num_transactions

    def large_itemsets(self, counts, min_support, num_transactions):
        return [(i, c) for (i, c) in counts.items() if (c / num_transactions) >= min_support]

    def candidate_itemset_counts(self, C_k, C_k_sets, counter, counts, row, transaction):
        # Assert that no items were found in this row
        found_any = False
        issubset = set.issubset  # Micro-optimization
        for candidate, candidate_set in zip(C_k, C_k_sets):
            # This is where most of the time is spent in the algorithm
            # If the candidate set is a subset, add count and mark the row
            if issubset(candidate_set, transaction):
                counts[candidate] += 1
                found_any = True
        return counts, found_any


class _CounterWithIds(_ItemsetCounter):
    def itemset_counter(self):
        return ItemsetCount()

    def get_count(self, count):
        return count.itemset_count

    def singleton_itemsets(self, get_transactions):
        counts = defaultdict(self.itemset_counter)
        num_transactions = 0
        for row, transaction in get_transactions():
            num_transactions += 1
            for item in transaction:
                counts[item].increment_count(row)
        return counts, num_transactions

    def large_itemsets(self, counts, min_support, num_transactions):
        return [(i, count) for (i, count) in counts.items() if (count.itemset_count / num_transactions) >= min_support]

    def candidate_itemset_counts(self, C_k, C_k_sets, counter, counts, row, transaction):
        # Assert that no items were found in this row
        found_any = False
        issubset = set.issubset  # Micro-optimization
        for candidate, candidate_set in zip(C_k, C_k_sets):
            # This is where most of the time is spent in the algorithm
            # If the candidate set is a subset, add count and mark the row
            if issubset(candidate_set, transaction):
                counts[candidate].increment_count(row)
                found_any = True
        return counts, found_any


def join_step(itemsets: typing.List[tuple]):
    """
    Join k length itemsets into k + 1 length itemsets.
    This algorithm assumes that the list of itemsets are sorted, and that the
    itemsets themselves are sorted tuples. Instead of always enumerating all
    n^2 combinations, the algorithm only has n^2 runtime for each block of
    itemsets with the first k - 1 items equal.
    Parameters
    ----------
    itemsets : list of itemsets
        A list of itemsets of length k, to be joined to k + 1 length
        itemsets.
    Examples
    --------
    >>> # This is an example from the 1994 paper by Agrawal et al.
    >>> itemsets = [(1, 2, 3), (1, 2, 4), (1, 3, 4), (1, 3, 5), (2, 3, 4)]
    >>> list(join_step(itemsets))
    [(1, 2, 3, 4), (1, 3, 4, 5)]
    """
    i = 0
    # Iterate over every itemset in the itemsets
    while i < len(itemsets):

        # The number of rows to skip in the while-loop, initially set to 1
        skip = 1

        # Get all but the last item in the itemset, and the last item
        *itemset_first, itemset_last = itemsets[i]

        # We now iterate over every itemset following this one, stopping
        # if the first k - 1 items are not equal. If we're at (1, 2, 3),
        # we'll consider (1, 2, 4) and (1, 2, 7), but not (1, 3, 1)

        # Keep a list of all last elements, i.e. tail elements, to perform
        # 2-combinations on later on
        tail_items = [itemset_last]
        tail_items_append = tail_items.append  # Micro-optimization

        # Iterate over ever itemset following this itemset
        for j in range(i + 1, len(itemsets)):

            # Get all but the last item in the itemset, and the last item
            *itemset_n_first, itemset_n_last = itemsets[j]

            # If it's the same, append and skip this itemset in while-loop
            if itemset_first == itemset_n_first:

                # Micro-optimization
                tail_items_append(itemset_n_last)
                skip += 1

            # If it's not the same, break out of the for-loop
            else:
                break

        # For every 2-combination in the tail items, yield a new candidate
        # itemset, which is sorted.
        itemset_first_tuple = tuple(itemset_first)
        for a, b in sorted(itertools.combinations(tail_items, 2)):
            yield itemset_first_tuple + (a,) + (b,)

        # Increment the while-loop counter
        i += skip


def prune_step(itemsets: typing.Iterable[tuple], possible_itemsets: typing.List[tuple]):
    """
    Prune possible itemsets whose subsets are not in the list of itemsets.
    Parameters
    ----------
    itemsets : list of itemsets
        A list of itemsets of length k.
    possible_itemsets : list of itemsets
        A list of possible itemsets of length k + 1 to be pruned.
    Examples
    -------
    >>> itemsets = [('a', 'b', 'c'), ('a', 'b', 'd'),
    ...             ('b', 'c', 'd'), ('a', 'c', 'd')]
    >>> possible_itemsets = list(join_step(itemsets))
    >>> list(prune_step(itemsets, possible_itemsets))
    [('a', 'b', 'c', 'd')]
    """

    # For faster lookups
    itemsets = set(itemsets)

    # Go through every possible itemset
    for possible_itemset in possible_itemsets:

        # Remove 1 from the combination, same as k-1 combinations
        # The itemsets created by removing the last two items in the possible
        # itemsets must be part of the itemsets by definition,
        # due to the way the `join_step` function merges the sorted itemsets

        for i in range(len(possible_itemset) - 2):
            removed = possible_itemset[:i] + possible_itemset[i + 1 :]

            # If every k combination exists in the set of itemsets,
            # yield the possible itemset. If it does not exist, then it's
            # support cannot be large enough, since supp(A) >= supp(AB) for
            # all B, and if supp(S) is large enough, then supp(s) must be large
            # enough for every s which is a subset of S.
            # This is the downward-closure property of the support function.
            if removed not in itemsets:
                break

        # If we have not breaked yet
        else:
            yield possible_itemset


def apriori_gen(itemsets: typing.List[tuple]):
    """
    Compute all possible k + 1 length supersets from k length itemsets.
    This is done efficiently by using the downward-closure property of the
    support function, which states that if support(S) > k, then support(s) > k
    for every subset s of S.
    Parameters
    ----------
    itemsets : list of itemsets
        A list of itemsets of length k.
    Examples
    -------
    >>> # This is an example from the 1994 paper by Agrawal et al.
    >>> itemsets = [(1, 2, 3), (1, 2, 4), (1, 3, 4), (1, 3, 5), (2, 3, 4)]
    >>> possible_itemsets = list(join_step(itemsets))
    >>> list(prune_step(itemsets, possible_itemsets))
    [(1, 2, 3, 4)]
    """
    possible_extensions = join_step(itemsets)
    yield from prune_step(itemsets, possible_extensions)


def itemsets_from_transactions(
    transactions: typing.Union[typing.List[tuple], typing.Callable],
    min_support: float,
    max_length: int = 8,
    verbosity: int = 0,
    output_transaction_ids: bool = False,
):
    """
    Compute itemsets from transactions by building the itemsets bottom up and
    iterating over the transactions to compute the support repedately. This is
    the heart of the Apriori algorithm by Agrawal et al. in the 1994 paper.
    Parameters
    ----------
    transactions : a list of itemsets (tuples with hashable entries),
                   or a function returning a generator
        A list of transactions. They can be of varying size. To pass through
        data without reading everything into memory at once, a callable
        returning a generator may also be passed.
    min_support : float
        The minimum support of the itemsets, i.e. the minimum frequency as a
        percentage.
    max_length : int
        The maximum length of the itemsets.
    verbosity : int
        The level of detail printing when the algorithm runs. Either 0, 1 or 2.
    output_transaction_ids : bool
        If set to true, the output contains the ids of transactions that
        contain a frequent itemset. The ids are the enumeration of the
        transactions in the sequence they appear.
    Examples
    --------
    >>> # This is an example from the 1994 paper by Agrawal et al.
    >>> transactions = [(1, 3, 4), (2, 3, 5), (1, 2, 3, 5), (2, 5)]
    >>> itemsets, _ = itemsets_from_transactions(transactions, min_support=2/5)
    >>> itemsets[1] == {(1,): 2, (2,): 3, (3,): 3, (5,): 3}
    True
    >>> itemsets[2] == {(1, 3): 2, (2, 3): 2, (2, 5): 3, (3, 5): 2}
    True
    >>> itemsets[3] == {(2, 3, 5): 2}
    True
    """

    # STEP 0 - Sanitize user inputs
    # -----------------------------
    if not (isinstance(min_support, numbers.Number) and (0 <= min_support <= 1)):
        raise ValueError("`min_support` must be a number between 0 and 1.")

    counter: typing.Union[_CounterWithIds, _Counter]  # Type info for mypy
    counter = _CounterWithIds() if (transactions and output_transaction_ids) else _Counter()

    wrong_transaction_type_msg = "`transactions` must be an iterable or a " "callable returning an iterable."

    if not transactions:
        return dict(), 0  # large_itemsets, num_transactions

    if isinstance(transactions, collections.abc.Iterable):

        def transaction_rows():
            for count, t in enumerate(transactions):
                yield count, set(t)

    # Assume the transactions is a callable, returning a generator
    elif callable(transactions):

        def transaction_rows():
            for count, t in enumerate(transactions()):
                yield count, set(t)

        if not isinstance(transactions(), collections.abc.Generator):
            raise TypeError(wrong_transaction_type_msg)
    else:
        raise TypeError(wrong_transaction_type_msg)

    # Keep a dictionary stating whether to consider the row, this will allow
    # row-pruning later on if no information was retrieved earlier from it
    use_transaction: typing.DefaultDict[int, bool] = defaultdict(lambda: True)

    # STEP 1 - Generate all large itemsets of size 1
    # ----------------------------------------------
    if verbosity > 0:
        print("Generating itemsets.")
        print(" Counting itemsets of length 1.")

    counts, num_transactions = counter.singleton_itemsets(transaction_rows)

    large_itemsets = counter.large_itemsets(counts, min_support, num_transactions)

    if verbosity > 0:
        num_cand, num_itemsets = len(counts.items()), len(large_itemsets)
        print("  Found {} candidate itemsets of length 1.".format(num_cand))
        print("  Found {} large itemsets of length 1.".format(num_itemsets))
    if verbosity > 1:
        print("    {}".format(list((i,) for (i, counts) in large_itemsets)))

    # If large itemsets were found, convert to dictionary
    if large_itemsets:
        large_itemsets = {1: {(i,): counts for (i, counts) in (large_itemsets)}}
    # No large itemsets were found, return immediately
    else:
        return dict(), 0  # large_itemsets, num_transactions

    # STEP 2 - Build up the size of the itemsets
    # ------------------------------------------

    # While there are itemsets of the previous size
    k = 2
    while large_itemsets[k - 1] and (max_length != 1):
        if verbosity > 0:
            print(" Counting itemsets of length {}.".format(k))

        # STEP 2a) - Build up candidate of larger itemsets

        # Retrieve the itemsets of the previous size, i.e. of size k - 1
        # They must be sorted to maintain the invariant when joining/pruning
        itemsets_list = sorted(large_itemsets[k - 1].keys())

        # Gen candidates of length k + 1 by joining, prune, and copy as set
        C_k = list(apriori_gen(itemsets_list))
        C_k_sets = [set(itemset) for itemset in C_k]

        if verbosity > 0:
            print("  Found {} candidate itemsets of length {}.".format(len(C_k), k))
        if verbosity > 1:
            print("   {}".format(C_k))

        # If no candidate itemsets were found, break out of the loop
        if not C_k:
            break

        # Prepare counts of candidate itemsets (from the prune step)
        counts = defaultdict(counter.itemset_counter)
        if verbosity > 1:
            print("    Iterating over transactions.")
        for row, transaction in transaction_rows():

            # If we've excluded this transaction earlier, do not consider it
            if not use_transaction[row]:
                continue

            counts, found_any = counter.candidate_itemset_counts(C_k, C_k_sets, counter, counts, row, transaction)

            # If no candidate sets were found in this row, skip this row of
            # transactions in the future
            if not found_any:
                use_transaction[row] = False

        # Only keep the candidates whose support is over the threshold
        C_k = counter.large_itemsets(counts, min_support, num_transactions)

        # If no itemsets were found, break out of the loop
        if not C_k:
            break

        # Candidate itemsets were found, add them and progress the while-loop
        large_itemsets[k] = {i: counts for (i, counts) in C_k}

        if verbosity > 0:
            num_found = len(large_itemsets[k])
            pp = "  Found {} large itemsets of length {}.".format(num_found, k)
            print(pp)
        if verbosity > 1:
            print("   {}".format(list(large_itemsets[k].keys())))
        k += 1

        # Break out if we are about to consider larger itemsets than the max
        if k > max_length:
            break

    if verbosity > 0:
        print("Itemset generation terminated.\n")

    return large_itemsets, num_transactions



In [61]:
"""
Implementations of algorithms related to association rules.
"""

import typing
import numbers
import itertools


class Rule(object):
    """
    A class for a rule.
    """

    # Number of decimals used for printing
    _decimals = 3

    def __init__(
        self,
        lhs: tuple,
        rhs: tuple,
        count_full: int = 0,
        count_lhs: int = 0,
        count_rhs: int = 0,
        num_transactions: int = 0,
    ):
        """
        Initialize a new rule. This call is a thin wrapper around some data.
        Parameters
        ----------
        lhs : tuple
            The left hand side (antecedent) of the rule. Each item in the tuple
            must be hashable, e.g. a string or an integer.
        rhs : tuple
            The right hand side (consequent) of the rule.
        count_full : int
            The count of the union of the lhs and rhs in the dataset.
        count_lhs : int
            The count of the lhs in the dataset.
        count_rhs : int
            The count of the rhs in the dataset.
        num_transactions : int
            The number of transactions in the dataset.
        Examples
        --------
        >>> r = Rule(('a', 'b'), ('c',), 50, 100, 150, 200)
        >>> r.confidence  # Probability of 'c', given 'a' and 'b'
        0.5
        >>> r.support  # Probability of ('a', 'b', 'c') in the data
        0.25
        >>> # Ratio of observed over expected support if lhs, rhs = independent
        >>> r.lift == 2 / 3
        True
        >>> print(r)
        {a, b} -> {c} (conf: 0.500, supp: 0.250, lift: 0.667, conv: 0.500)
        >>> r
        {a, b} -> {c}
        """
        self.lhs = lhs  # antecedent
        self.rhs = rhs  # consequent
        self.count_full = count_full
        self.count_lhs = count_lhs
        self.count_rhs = count_rhs
        self.num_transactions = num_transactions

    @property
    def confidence(self):
        """
        The confidence of a rule is the probability of the rhs given the lhs.
        If X -> Y, then the confidence is P(Y|X).
        """
        try:
            return self.count_full / self.count_lhs
        except ZeroDivisionError:
            return None
        except AttributeError:
            return None

    @property
    def support(self):
        """
        The support of a rule is the frequency of which the lhs and rhs appear
        together in the dataset. If X -> Y, then the support is P(Y and X).
        """
        try:
            return self.count_full / self.num_transactions
        except ZeroDivisionError:
            return None
        except AttributeError:
            return None

    @property
    def lift(self):
        """
        The lift of a rule is the ratio of the observed support to the expected
        support if the lhs and rhs were independent.If X -> Y, then the lift is
        given by the fraction P(X and Y) / (P(X) * P(Y)).
        """
        try:
            observed_support = self.count_full / self.num_transactions
            prod_counts = self.count_lhs * self.count_rhs
            expected_support = prod_counts / self.num_transactions ** 2
            return observed_support / expected_support
        except ZeroDivisionError:
            return None
        except AttributeError:
            return None

    @property
    def conviction(self):
        """
        The conviction of a rule X -> Y is the ratio P(not Y) / P(not Y | X).
        It's the proportion of how often Y does not appear in the data to how
        often Y does not appear in the data, given X. If the ratio is large,
        then the confidence is large and Y appears often.
        """
        try:
            eps = 10e-10  # Avoid zero division
            prob_not_rhs = 1 - self.count_rhs / self.num_transactions
            prob_not_rhs_given_lhs = 1 - self.confidence
            return prob_not_rhs / (prob_not_rhs_given_lhs + eps)
        except ZeroDivisionError:
            return None
        except AttributeError:
            return None

    @property
    def rpf(self):
        """
        The RPF (Rule Power Factor) is the confidence times the support.
        """
        try:
            return self.confidence * self.support
        except ZeroDivisionError:
            return None
        except AttributeError:
            return None

    @staticmethod
    def _pf(s):
        """
        Pretty formatting of an iterable.
        """
        return "{" + ", ".join(str(k) for k in s) + "}"

    def __repr__(self):
        """
        Representation of a rule.
        """
        return "{} -> {}".format(self._pf(self.lhs), self._pf(self.rhs))

    def __str__(self):
        """
        Printing of a rule.
        """
        conf = "conf: {0:.3f}".format(self.confidence)
        supp = "supp: {0:.3f}".format(self.support)
        lift = "lift: {0:.3f}".format(self.lift)
        conv = "conv: {0:.3f}".format(self.conviction)

        return "{} -> {} ({}, {}, {}, {})".format(self._pf(self.lhs), self._pf(self.rhs), conf, supp, lift, conv)

    def __eq__(self, other):
        """
        Equality of two rules.
        """
        return (set(self.lhs) == set(other.lhs)) and (set(self.rhs) == set(other.rhs))

    def __hash__(self):
        """
        Hashing a rule for efficient set and dict representation.
        """
        return hash(frozenset(self.lhs + self.rhs))

    def __len__(self):
        """
        The length of a rule, defined as the number of items in the rule.
        """
        return len(self.lhs + self.rhs)


def generate_rules_simple(
    itemsets: typing.Dict[int, typing.Dict],
    min_confidence: float,
    num_transactions: int,
):
    """
    DO NOT USE. This is a simple top-down algorithm for generating association
    rules. It is included here for testing purposes, and because it is
    mentioned in the 1994 paper by Agrawal et al. It is slow because it does
    not enumerate the search space efficiently: it produces duplicates, and it
    does not prune the search space efficiently.
    Simple algorithm for generating association rules from itemsets.
    """

    # Iterate over every size
    for size in itemsets.keys():

        # Do not consider itemsets of size 1
        if size < 2:
            continue

        # This algorithm returns duplicates, so we keep track of items yielded
        # in a set to avoid yielding duplicates
        yielded: set = set()
        yielded_add = yielded.add

        # Iterate over every itemset of the prescribed size
        for itemset in itemsets[size].keys():

            # Generate rules
            for result in _genrules(itemset, itemset, itemsets, min_confidence, num_transactions):

                # If the rule has been yieded, keep going, else add and yield
                if result in yielded:
                    continue
                else:
                    yielded_add(result)
                    yield result


def _genrules(l_k, a_m, itemsets, min_conf, num_transactions):
    """
    DO NOT USE. This is the gen-rules algorithm from the 1994 paper by Agrawal
    et al. It's a subroutine called by `generate_rules_simple`. However, the
    algorithm `generate_rules_simple` should not be used.
    The naive algorithm from the original paper.
    Parameters
    ----------
    l_k : tuple
        The itemset containing all elements to be considered for a rule.
    a_m : tuple
        The itemset to take m-length combinations of, an move to the left of
        l_k. The itemset a_m is a subset of l_k.
    """

    def count(itemset):
        """
        Helper function to retrieve the count of the itemset in the dataset.
        """
        return itemsets[len(itemset)][itemset]

    # Iterate over every k - 1 combination of a_m to produce
    # rules of the form a -> (l - a)
    for a_m in itertools.combinations(a_m, len(a_m) - 1):

        # Compute the count of this rule, which is a_m -> (l_k - a_m)
        confidence = count(l_k) / count(a_m)

        # Keep going if the confidence level is too low
        if confidence < min_conf:
            continue

        # Create the right hand set: rhs = (l_k - a_m) , and keep it sorted
        rhs = set(l_k).difference(set(a_m))
        rhs = tuple(sorted(rhs))

        # Create new rule object and yield it
        yield Rule(a_m, rhs, count(l_k), count(a_m), count(rhs), num_transactions)

        # If the left hand side has one item only, do not recurse the function
        if len(a_m) <= 1:
            continue
        yield from _genrules(l_k, a_m, itemsets, min_conf, num_transactions)


def generate_rules_apriori(
    itemsets: typing.Dict[int, typing.Dict[tuple, int]],
    min_confidence: float,
    num_transactions: int,
    verbosity: int = 0,
):
    """
    Bottom up algorithm for generating association rules from itemsets, very
    similar to the fast algorithm proposed in the original 1994 paper by
    Agrawal et al.
    The algorithm is based on the observation that for {a, b} -> {c, d} to
    hold, both {a, b, c} -> {d} and {a, b, d} -> {c} must hold, since in
    general conf( {a, b, c} -> {d} ) >= conf( {a, b} -> {c, d} ).
    In other words, if either of the two one-consequent rules do not hold, then
    there is no need to ever consider the two-consequent rule.
    Parameters
    ----------
    itemsets : dict of dicts
        The first level of the dictionary is of the form (length, dict of item
        sets). The second level is of the form (itemset, count_in_dataset)).
    min_confidence :  float
        The minimum confidence required for the rule to be yielded.
    num_transactions : int
        The number of transactions in the data set.
    verbosity : int
        The level of detail printing when the algorithm runs. Either 0, 1 or 2.
    Examples
    --------
    >>> itemsets = {1: {('a',): 3, ('b',): 2, ('c',): 1},
    ...             2: {('a', 'b'): 2, ('a', 'c'): 1}}
    >>> list(generate_rules_apriori(itemsets, 1.0, 3))
    [{b} -> {a}, {c} -> {a}]
    """
    # Validate user inputs
    if not ((0 <= min_confidence <= 1) and isinstance(min_confidence, numbers.Number)):
        raise ValueError("`min_confidence` must be a number between 0 and 1.")

    if not ((num_transactions >= 0) and isinstance(num_transactions, numbers.Number)):
        raise ValueError("`num_transactions` must be a number greater than 0.")

    def count(itemset):
        """
        Helper function to retrieve the count of the itemset in the dataset.
        """
        return itemsets[len(itemset)][itemset]

    if verbosity > 0:
        print("Generating rules from itemsets.")

    # For every itemset of a perscribed size
    for size in itemsets.keys():

        # Do not consider itemsets of size 1
        if size < 2:
            continue

        if verbosity > 0:
            print(" Generating rules of size {}.".format(size))

        # For every itemset of this size
        for itemset in itemsets[size].keys():

            # Special case to capture rules such as {others} -> {1 item}
            for removed in itertools.combinations(itemset, 1):

                # Compute the left hand side
                remaining = set(itemset).difference(set(removed))
                lhs = tuple(sorted(remaining))

                # If the confidence is high enough, yield the rule
                conf = count(itemset) / count(lhs)
                if conf >= min_confidence:
                    yield Rule(
                        lhs,
                        removed,
                        count(itemset),
                        count(lhs),
                        count(removed),
                        num_transactions,
                    )

            # Generate combinations to start off of. These 1-combinations will
            # be merged to 2-combinations in the function `_ap_genrules`
            H_1 = list(itertools.combinations(itemset, 1))
            yield from _ap_genrules(itemset, H_1, itemsets, min_confidence, num_transactions)

    if verbosity > 0:
        print("Rule generation terminated.\n")


def _ap_genrules(
    itemset: tuple,
    H_m: typing.List[tuple],
    itemsets: typing.Dict[int, typing.Dict[tuple, int]],
    min_conf: float,
    num_transactions: int,
):
    """
    Recursively build up rules by adding more items to the right hand side.
    This algorithm is called `ap-genrules` in the original paper. It is
    called by the `generate_rules_apriori` generator above. See it's docs.
    Parameters
    ----------
    itemset : tuple
        The itemset under consideration.
    H_m : tuple
        Subsets of the itemset of length m, to be considered for rhs of a rule.
    itemsets : dict of dicts
        All itemsets and counts for in the data set.
    min_conf : float
        The minimum confidence for a rule to be returned.
    num_transactions : int
        The number of transactions in the data set.
    """

    def count(itemset):
        """
        Helper function to retrieve the count of the itemset in the dataset.
        """
        return itemsets[len(itemset)][itemset]

    # If H_1 is so large that calling `apriori_gen` will produce right-hand
    # sides as large as `itemset`, there will be no right hand side.
    # This should not happen happen, so we return.
    if len(itemset) <= (len(H_m[0]) + 1):
        return

    # Generate right-hand itemsets of length k + 1 if H is of length k
    H_m = list(apriori_gen(H_m))
    H_m_copy = H_m.copy()

    # For every possible right hand side
    for h_m in H_m:

        # Compute the left hand side of the rule
        lhs = tuple(sorted(set(itemset).difference(set(h_m))))

        # If the confidence is high enough, yield the rule, else remove from
        # the upcoming recursive generator call
        if (count(itemset) / count(lhs)) >= min_conf:
            yield Rule(
                lhs,
                h_m,
                count(itemset),
                count(lhs),
                count(h_m),
                num_transactions,
            )
        else:
            H_m_copy.remove(h_m)

    # Unless the list of right-hand sides is empty, recurse the generator call
    if H_m_copy:
        yield from _ap_genrules(itemset, H_m_copy, itemsets, min_conf, num_transactions)


In [62]:
def data_generator(filename):
  """
  Data generator, needs to return a generator to be called several times.
  Use this approach if data is too large to fit in memory. If not use a list.
  """
  def data_gen():
    with open(filename) as file:
      for line in file:
        yield tuple(k.strip() for k in line.split(','))      

  return data_gen

transactions = data_generator('testr.csv')

itemsets, rules = apriori(transactions, min_support=0.9, min_confidence=0.6)


In [66]:
itemsets, rules = apriori(lis, min_support=0.9, min_confidence=0.6)


ValueError: The truth value of an array with more than one element is ambiguous. Use a.any() or a.all()

In [67]:
import pandas as pd


# The data set has missing values
df = pd.read_csv("testr.csv") # Data has shape approximately (1000, 60)

# Get the columns a strings
columns = list(df.columns)

transactions = []  # Prepare a list of transactions

# Loop over every row in the DataFrame to collect transactions
for i in range(len(df)):
    
    # Encode values as e.g., 'col1=N/A' and 'col2=male'.
    # We include column names to differentiate between values such as
    # 'col1=N/A' and 'col2=N/A', since they might mean different things
    # in the analysis (and might not be missing at random)
    values = list(t.strip() for t in df.iloc[i, :].fillna("N/A").values)
    transaction = tuple(f"{column}={value}" for column, value in zip(columns, values))

    # Add transaction to transactions
    transactions.append(transaction)

itemsets, rules = apriori(transactions, min_support=0.8,
                            min_confidence=0.5, max_length=6, verbosity=1)


AttributeError: 'numpy.int64' object has no attribute 'strip'

In [75]:
"""
Problem 2: Multi-Hash Algorithm
Hashing Function 1: i * j * ... * z mod bucket_size
Hashing Function 2: i + j + ... + z mod bucket_size
Executing code: 
1) $ python multihash.py input.txt 4 5
2) $ python multihash.py input1.txt 20 5
"""
import sys
import re

def multihash(inputfile, support, bucket_size):
    result = {}
    candidates = []
    step = 1
    while 1:
        ans_one = pass_one(inputfile, candidates, support, bucket_size)
        ans_two = pass_two(inputfile, ans_one, bucket_size)
        frequent_items = ans_two[0]
        result.setdefault(step, [])
        result[step].append(ans_two[0])
        if len(ans_two) == 1:
            break
        buckets = ans_one[1]
        candidates = ans_two[2]
        if not candidates:
            break
        result.setdefault(step+1, [])
        result[step+1].append(buckets)
        step += 1
    # print result
    display_result(result)
    return result

def display_result(result):
    for (k, v) in result.items():
        if k == 1:
            itemsets = v[0]
            tmp = []
            for item in itemsets:
                tmp.append(item[0])
            print("\n", tmp, "\n")
        else:
            
            bucket_counts = v[0]
            itemsets = v[1]
            for bucket_count in bucket_counts:
                print(bucket_count)
            print(itemsets, "\n")
    print("\n")

def pass_one(inputfile, candidates, support, bucket_size):
    result = []
    itemset_size = 1
    if candidates:
        itemset_size = len(candidates[0])
    baskets = generate_baskets(inputfile)
    item_counts = count_items(candidates, support, baskets)
    frequent_items = generate_frequent_items(item_counts, support)
    result.append(frequent_items)
    pairs = generate_pairs(frequent_items, baskets, itemset_size + 1)
    if not pairs:
        return result
    buckets = hash_pairs(pairs, baskets, bucket_size)
    result.append(buckets)

    bitmap_one = generate_bitmap(buckets[0], support)
    bitmap_two = generate_bitmap(buckets[1], support)

    result.append([bitmap_one, bitmap_two])
    return result

def pass_two(inputfile, ans_one, bucket_size):
    result = []
    frequent_items = ans_one[0]
    result.append(frequent_items)
    if len(ans_one) == 1:
        return result

    bitmaps = ans_one[2]
    itemset_size = len(frequent_items[0]) + 1
    baskets = generate_baskets(inputfile)
    pairs = generate_pairs(frequent_items, baskets, itemset_size + 1)
    buckets = maping_pairs_bucket(pairs, baskets, bucket_size)

    candidates_one = get_candidates(buckets[0], bitmaps[0])
    candidates_two = get_candidates(buckets[1], bitmaps[1])

    candidates = []
    for item in candidates_one:
        if item in candidates_two:
            candidates.append(item)
    result.append(buckets)
    result.append(candidates)
    return result

def get_candidates(bucket, bitmap):
    bitmap_list = bitmap_to_list(bitmap)
    candidates = []
    for i in range(len(bitmap_list)):
        digit = bitmap_list[i]
        if digit == 1:
            for item in bucket[i]:
                candidates.append(item)
    return candidates

def bitmap_to_list(bitmap):
    bitmap_str = str(bin(bitmap))
    slen = len(bitmap_str)
    result = []
    for i in range(0, slen - 2):
        digit = int(bitmap_str[slen - 1 - i])
        result.append(digit)
    return result

def generate_frequent_items(item_counts, support):
    itemset_size = len(item_counts[0]) - 1
    frequent_items = []
    for item in item_counts:
        if item[itemset_size] >= support:
            frequent_items.append(item[:-1])
    frequent_items.sort()
    return frequent_items

def count_items(candidates, support, baskets):
    itemset_size = 1
    result = []
    if candidates:
        itemset_size = len(candidates[0])
    if not candidates:
        ht_item = {}  
        for basket in baskets:
            for item in basket:
                ht_item.setdefault(item, 0)
                ht_item[item] += 1

        for (item, count) in ht_item.items():
            result.append([item, count])
    else:
        result = candidates
    return result

def generate_bitmap(bucket, support):
    bitmap = 0
    for (k, v) in bucket.items():
        if v >= support:
            bitmap += 1 << k
    return bitmap

def generate_baskets(inputfile):

    inputdata = open(inputfile, 'rU')

    baskets = []
    for line in inputdata:
        basket = []
        for item in line: # or basket[:-1] to delete '\n'
            if item == ' ' or item == ',' or item == '\n':
                continue
            basket.append(item)
        baskets.append(basket)
    return baskets

def maping_pairs_bucket(pairs, baskets, bucket_size):
    pair_size = len(pairs[0])
    ht_item_to_num = numbering(pairs)
    count_pairs(pairs, baskets)
    bucket_one = hash_function_one(pairs, ht_item_to_num, bucket_size)
    bucket_two = hash_function_two(pairs, ht_item_to_num, bucket_size)
    return [bucket_one, bucket_two]

def hash_function_one(pairs, ht_item_to_num, bucket_size):
    pair_size = len(pairs[0]) - 1
    bucket = {} # key: bucket_no, value: pairs
    for pair in pairs:
        bucket_no = 1
        for i in range(pair_size):
            c = pair[i]
            bucket_no *= ht_item_to_num[c]
        bucket_no %= bucket_size

        bucket.setdefault(bucket_no, [])
        bucket[bucket_no].append(pair)
    return bucket

def hash_function_two(pairs, ht_item_to_num, bucket_size):
    pair_size = len(pairs[0]) - 1
    bucket = {} # key: bucket_no, value: pairs
    for pair in pairs:
        bucket_no = 1
        for i in range(pair_size):
            c = pair[i]
            bucket_no += ht_item_to_num[c]
        bucket_no %= bucket_size

        bucket.setdefault(bucket_no, [])
        bucket[bucket_no].append(pair)
    return bucket


def hash_pairs(pairs, baskets, bucket_size):
    pair_size = len(pairs[0])
    buckets = maping_pairs_bucket(pairs, baskets, bucket_size)
    for bucket in buckets:
        count_bucket(pair_size, bucket, bucket_size)
    return buckets

def count_bucket(pair_size, bucket, bucket_size):
    for (k, v) in bucket.items():
        count = 0
        for item in v:
            count += item[pair_size]
        bucket[k] = count
    for i in range(bucket_size):
        bucket.setdefault(i, 0)
    [(k,bucket[k]) for k in sorted(bucket.keys())]

def count_pairs(pairs, baskets):
    itemset_size = len(pairs[0])
    for pair in pairs:
        count = 0
        for basket in baskets:
            if len(basket) < itemset_size:
                continue
            inside = True
            for i in range(len(pair)):
                if pair[i] not in basket:
                    inside = False
                    break
            if inside == True:
                count += 1
        pair.append(count)

def numbering(pairs):
    ht_item_to_num = {}
    number = 1
    for pair in pairs:      # O(n), since length of pair is constant
        for c in pair:
            if c not in ht_item_to_num.keys():
                ht_item_to_num.setdefault(c, number)
                number += 1
    return ht_item_to_num

def generate_singletons(itemsets):
    ht = {}
    for items in itemsets:
        for item in items:
            ht.setdefault(item, 0)
    keys = ht.keys()
    #keys.sort()
    sorted(ht.keys())
    return keys

def generate_pairs(frequent_items, baskets, itemset_size):
    result = []
    frequent_item_processed = []    # avoid case like ab ba
    frequent_singletons = generate_singletons(frequent_items)
    for frequent_item in frequent_items:
        ht = {}
        for basket in baskets:
            if len(basket) < itemset_size + 1:
                continue
            inside = True
            for item in frequent_item:
                if item not in basket:
                    inside = False
                    break
            if inside == True:
                for item in basket:
                    if (item not in frequent_singletons) or (item in frequent_item):
                        continue
                    ht.setdefault(item, 0)
        keys = ht.keys()
        #keys.sort()
        sorted(ht.keys())
        for key in keys:
            tmp = list(frequent_item)
            tmp.extend(key)
            tmp.sort()
            if tmp not in result:
                result.append(tmp)
        frequent_item_processed.append(frequent_item)
    true_result = []
    for items in result:
        inside = True
        for i in range(len(items)):
            tmp = list(items)
            tmp.pop(i)
            if tmp not in frequent_items:
                inside = False
                break
        if inside == True:
            true_result.append(items)
    return true_result


In [77]:
multihash('apr_impr.txt', 4, 5)


 ['a', 'b', 'c', 'd', 'e', 'f', 'g'] 

{2: 17, 3: 14, 4: 17, 0: 32, 1: 14}
{4: 15, 0: 17, 1: 25, 2: 18, 3: 19}
[['a', 'b'], ['a', 'c'], ['a', 'e'], ['a', 'f'], ['b', 'c'], ['b', 'd'], ['b', 'e'], ['b', 'f'], ['c', 'e'], ['c', 'f'], ['c', 'g'], ['d', 'e'], ['e', 'f'], ['f', 'g']] 

{1: 3, 3: 5, 2: 3, 0: 16, 4: 7}
{2: 5, 3: 7, 4: 7, 1: 7, 0: 8}
[['a', 'b', 'c'], ['a', 'c', 'e'], ['b', 'd', 'e'], ['c', 'f', 'g']] 





C:\Users\HP\anaconda3\lib\site-packages\ipykernel_launcher.py:152: DeprecationWarning: 'U' mode is deprecated


{1: [[['a'], ['b'], ['c'], ['d'], ['e'], ['f'], ['g']]],
 2: [[{2: 17, 3: 14, 4: 17, 0: 32, 1: 14},
   {4: 15, 0: 17, 1: 25, 2: 18, 3: 19}],
  [['a', 'b'],
   ['a', 'c'],
   ['a', 'e'],
   ['a', 'f'],
   ['b', 'c'],
   ['b', 'd'],
   ['b', 'e'],
   ['b', 'f'],
   ['c', 'e'],
   ['c', 'f'],
   ['c', 'g'],
   ['d', 'e'],
   ['e', 'f'],
   ['f', 'g']]],
 3: [[{1: 3, 3: 5, 2: 3, 0: 16, 4: 7}, {2: 5, 3: 7, 4: 7, 1: 7, 0: 8}],
  [['a', 'b', 'c'], ['a', 'c', 'e'], ['b', 'd', 'e'], ['c', 'f', 'g']]]}

In [81]:
multihash('adult.data', 19000, 100)

C:\Users\HP\anaconda3\lib\site-packages\ipykernel_launcher.py:152: DeprecationWarning: 'U' mode is deprecated


KeyboardInterrupt: 